In [1]:
import pandas as pd
import numpy as np
import re
import json
import numpy as np
import timeit 
from datetime import datetime

In [2]:
import tensorflow as tf
from tensorflow import keras

In [42]:
# Cufflinks wrapper on plotly
import cufflinks
from IPython.core.interactiveshell import InteractiveShell
InteractiveShell.ast_node_interactivity = 'all'

from plotly.offline import iplot
cufflinks.go_offline()

# Set global theme

import plotly.figure_factory as ff

import plotly.graph_objects as go
import plotly.express as px

In [4]:
from sklearn.model_selection import train_test_split

In [5]:
#Selecting a central city point to center all graphs around - Swietokrzyska Subway 
center_coors=52.235176, 21.008393

In [6]:
df=pd.read_excel("RE_models_input.xlsx")

In [7]:
df.columns

Index(['Id', 'Area', 'Price', 'latitude', 'longitude', 'build_year',
       'building_floors_num', 'rooms_num', 'City', 'subdistrict', 'market',
       'Building_material', 'Building_ownership', 'Building_type',
       'Construction_status', 'floor_no', 'Heating', 'Windows_type',
       'Equipment_types_dishwasher', 'Equipment_types_fridge',
       'Equipment_types_furniture', 'Equipment_types_oven',
       'Equipment_types_stove', 'Equipment_types_tv',
       'Equipment_types_washing_machine', 'Extras_types_air_conditioning',
       'Extras_types_attic', 'Extras_types_balcony', 'Extras_types_basement',
       'Extras_types_garage', 'Extras_types_garden', 'Extras_types_lift',
       'Extras_types_separate_kitchen', 'Extras_types_terrace',
       'Extras_types_two_storey', 'Extras_types_usable_room',
       'Media_types_cable-television', 'Media_types_electricity',
       'Media_types_internet', 'Media_types_phone', 'Media_types_sewage',
       'Media_types_water', 'Security_types_alarm

In [8]:
df['rooms_num']=np.where(df['rooms_num']=="more",10,df['rooms_num'])

In [9]:
df.drop(columns=['floor_no',"City","district_old",'price_decrease_from_20k','price_decrease_per_10min'],inplace=True)

In [10]:
df.columns

Index(['Id', 'Area', 'Price', 'latitude', 'longitude', 'build_year',
       'building_floors_num', 'rooms_num', 'subdistrict', 'market',
       'Building_material', 'Building_ownership', 'Building_type',
       'Construction_status', 'Heating', 'Windows_type',
       'Equipment_types_dishwasher', 'Equipment_types_fridge',
       'Equipment_types_furniture', 'Equipment_types_oven',
       'Equipment_types_stove', 'Equipment_types_tv',
       'Equipment_types_washing_machine', 'Extras_types_air_conditioning',
       'Extras_types_attic', 'Extras_types_balcony', 'Extras_types_basement',
       'Extras_types_garage', 'Extras_types_garden', 'Extras_types_lift',
       'Extras_types_separate_kitchen', 'Extras_types_terrace',
       'Extras_types_two_storey', 'Extras_types_usable_room',
       'Media_types_cable-television', 'Media_types_electricity',
       'Media_types_internet', 'Media_types_phone', 'Media_types_sewage',
       'Media_types_water', 'Security_types_alarm',
       'Security_

In [11]:
df["distance_driving"]=(df.distance_driving_8AM+df.distance_return_driving_5PM)/2
df["distance_transit"]=(df.distance_transit_8AM+df.distance_return_transit_5PM)/2
df["time_driving"]=(df.time_driving_8AM+df.time_return_driving_5PM)/2
df["time_transit"]=(df.time_return_transit_5PM+df.time_transit_8AM)/2

In [12]:
df.drop(columns=['distance_transit_8AM', 'time_transit_8AM', 'distance_driving_8AM',
       'time_driving_8AM', 'distance_return_transit_5PM',
       'time_return_transit_5PM', 'distance_return_driving_5PM',
       'time_return_driving_5PM'],inplace=True)

# Data exploration

## Category composition

In [15]:
unique_features=["district","market","Building_material","Building_ownership","Building_type","Construction_status","Heating",
"Windows_type"]

In [15]:
for feature in unique_features:
    feature_list=["Id"]
    feature_list.append(feature)

    df_temp=df[feature_list].groupby(feature, as_index=False).count()
    df_temp.rename(columns={"Id":"share"},inplace=True)
    df_temp.sort_values(by="share",inplace=True, ascending=False)
    df_temp["share"]=df_temp["share"]/df.shape[0]
    df_temp["share"]=np.around(df_temp["share"],3)*100
    df_temp["colour"]=np.where(df_temp[feature]=="not_specified","missing_data","valid_data")
    
    fig = px.bar(df_temp, x=feature, y='share', color="colour",
                 color_discrete_sequence=["blue", "red"],
                 category_orders={"colour": ["valid_data", "missing_data"]},)
    print("\n Feature summary for {} - Share of category within whole sample".format(feature))
    fig.show()
    print("----------------------------------------------------------------------------------------------------------------------------\n\n\n")

    


 Feature summary for district - Share of category within whole sample


----------------------------------------------------------------------------------------------------------------------------




 Feature summary for market - Share of category within whole sample


----------------------------------------------------------------------------------------------------------------------------




 Feature summary for Building_material - Share of category within whole sample


----------------------------------------------------------------------------------------------------------------------------




 Feature summary for Building_ownership - Share of category within whole sample


----------------------------------------------------------------------------------------------------------------------------




 Feature summary for Building_type - Share of category within whole sample


----------------------------------------------------------------------------------------------------------------------------




 Feature summary for Construction_status - Share of category within whole sample


----------------------------------------------------------------------------------------------------------------------------




 Feature summary for Heating - Share of category within whole sample


----------------------------------------------------------------------------------------------------------------------------




 Feature summary for Windows_type - Share of category within whole sample


----------------------------------------------------------------------------------------------------------------------------





## Average unit price by feature 

In [16]:
for feature in unique_features:
    feature_list=["unit_price"]
    feature_list.append(feature)

    df_temp=df[feature_list]
    
    print("\n Unit price distribution in split by {}".format(feature))
    
    fig = fig = px.box(df_temp, y="unit_price", x=feature, points="suspectedoutliers");
    fig.update_yaxes(range=[5000, 25000])


    print("----------------------------------------------------------------------------------------------------------------------------\n\n\n")

    


 Unit price distribution in split by district


----------------------------------------------------------------------------------------------------------------------------




 Unit price distribution in split by market


----------------------------------------------------------------------------------------------------------------------------




 Unit price distribution in split by Building_material


----------------------------------------------------------------------------------------------------------------------------




 Unit price distribution in split by Building_ownership


----------------------------------------------------------------------------------------------------------------------------




 Unit price distribution in split by Building_type


----------------------------------------------------------------------------------------------------------------------------




 Unit price distribution in split by Construction_status


----------------------------------------------------------------------------------------------------------------------------




 Unit price distribution in split by Heating


----------------------------------------------------------------------------------------------------------------------------




 Unit price distribution in split by Windows_type


----------------------------------------------------------------------------------------------------------------------------





# Transforming data for ML models

In [16]:
from sklearn.preprocessing import OneHotEncoder

In [17]:
df_cat=df[unique_features]

In [18]:
enc=OneHotEncoder()
enc.fit(df_cat)

one_hot_val=enc.fit_transform(df_cat).toarray().astype(int)
one_hot_columns=enc.get_feature_names(unique_features)

OneHotEncoder(categories='auto', drop=None, dtype=<class 'numpy.float64'>,
              handle_unknown='error', sparse=True)

In [19]:
df_one_hot=pd.DataFrame(one_hot_val, columns=one_hot_columns)

In [20]:
df_one_hot.columns

Index(['district_Bemowo', 'district_Bialoleka', 'district_Bielany',
       'district_Downtown', 'district_Mokotow', 'district_Ochota',
       'district_Praga', 'district_Southern Praga', 'district_Subburbs',
       'district_Targowek', 'district_Ursynow', 'district_Wawer',
       'district_Wilanow', 'district_Wlochy', 'district_Wola',
       'district_Zoliborz', 'market_primary', 'market_secondary',
       'Building_material_breezeblock', 'Building_material_brick',
       'Building_material_cellular_concrete', 'Building_material_concrete',
       'Building_material_concrete_plate', 'Building_material_hydroton',
       'Building_material_not_specified', 'Building_material_other',
       'Building_material_reinforced_concrete', 'Building_material_silikat',
       'Building_material_wood', 'Building_ownership_co_operative_ownership',
       'Building_ownership_co_operative_ownership_with_a_land_and_mortgage_registe',
       'Building_ownership_full_ownership', 'Building_ownership_not_spec

In [21]:
not_specified_idx=[]
for i in range(0,df_one_hot.columns.shape[0]):
    if "not_specified" in df_one_hot.columns[i]:
        not_specified_idx.append(i)
not_specified_idx=np.asarray(not_specified_idx)

Let's drop all "not_specified" columns and secondary market in Mokotow district (it will be used as baseline in models)

In [22]:
drop_collinear_cols=list(df_one_hot.columns[not_specified_idx])
drop_collinear_cols.append('district_Mokotow')
drop_collinear_cols.append('market_secondary')

In [23]:
def list_diff(list1, list2):
    out = []
    for ele in list1:
        if not ele in list2:
            out.append(ele)
    return out

In [24]:
df_one_hot.columns

Index(['district_Bemowo', 'district_Bialoleka', 'district_Bielany',
       'district_Downtown', 'district_Mokotow', 'district_Ochota',
       'district_Praga', 'district_Southern Praga', 'district_Subburbs',
       'district_Targowek', 'district_Ursynow', 'district_Wawer',
       'district_Wilanow', 'district_Wlochy', 'district_Wola',
       'district_Zoliborz', 'market_primary', 'market_secondary',
       'Building_material_breezeblock', 'Building_material_brick',
       'Building_material_cellular_concrete', 'Building_material_concrete',
       'Building_material_concrete_plate', 'Building_material_hydroton',
       'Building_material_not_specified', 'Building_material_other',
       'Building_material_reinforced_concrete', 'Building_material_silikat',
       'Building_material_wood', 'Building_ownership_co_operative_ownership',
       'Building_ownership_co_operative_ownership_with_a_land_and_mortgage_registe',
       'Building_ownership_full_ownership', 'Building_ownership_not_spec

In [25]:
df_cat_columns=list_diff(df_one_hot.columns,drop_collinear_cols)

In [26]:
df_cat=df_one_hot[df_cat_columns]

In [27]:
columns_base=list_diff(df.columns, unique_features)

In [28]:
drop_columns_base=[
    'Price','latitude','longitude','lon_mod','lat_mod','grid_price','sample_size','City','subdistrict'
                  ]

In [29]:
columns_base=list_diff(columns_base, drop_columns_base)

In [30]:
df_base=df[columns_base]

In [31]:
df_base.columns

Index(['Id', 'Area', 'build_year', 'building_floors_num', 'rooms_num',
       'Equipment_types_dishwasher', 'Equipment_types_fridge',
       'Equipment_types_furniture', 'Equipment_types_oven',
       'Equipment_types_stove', 'Equipment_types_tv',
       'Equipment_types_washing_machine', 'Extras_types_air_conditioning',
       'Extras_types_attic', 'Extras_types_balcony', 'Extras_types_basement',
       'Extras_types_garage', 'Extras_types_garden', 'Extras_types_lift',
       'Extras_types_separate_kitchen', 'Extras_types_terrace',
       'Extras_types_two_storey', 'Extras_types_usable_room',
       'Media_types_cable-television', 'Media_types_electricity',
       'Media_types_internet', 'Media_types_phone', 'Media_types_sewage',
       'Media_types_water', 'Security_types_alarm',
       'Security_types_anti_burglary_door', 'Security_types_closed_area',
       'Security_types_entryphone', 'Security_types_monitoring',
       'Security_types_roller_shutters', 'floor_num', 'unit_price',


## Combining data for modeling

In [32]:
ml_data=pd.concat([df_base,df_cat],axis=1)

In [33]:
ml_data.shape

(11788, 89)

In [34]:
ml_data.head()

Id   Area  build_year  building_floors_num rooms_num  \
0  60534950  80.10        2021                    8         4   
1  60534789  52.27        2021                    8         2   
2  60534636  64.63        2021                    8         3   
3  60441425  46.86        2020                   14         3   
4  60225257  57.40        2019                   11         3   

   Equipment_types_dishwasher  Equipment_types_fridge  \
0                           0                       0   
1                           0                       0   
2                           0                       0   
3                           0                       0   
4                           1                       1   

   Equipment_types_furniture  Equipment_types_oven  Equipment_types_stove  \
0                          0                     0                      0   
1                          0                     0                      0   
2                          0                     0                      0   
3                          0                     0                      0   
4                          1                     1                      1   

   ...  Construction_status_to_completion  Construction_status_to_renovation  \
0  ...                                  0                                  0   
1  ...                                  0                                  0   
2  ...                                  0                                  0   
3  ...                                  0                                  0   
4  ...                                  0                                  0   

   Heating_boiler_room  Heating_electrical  Heating_gas  Heating_other  \
0                    0                   0            0              0   
1                    0                   0            0              0   
2                    0                   0            0              0   
3                    0                   0            0              0   
4                    0                   0            0              0   

   Heating_urban  Windows_type_aluminium  Windows_type_plastic  \
0              0                       0                     0   
1              0                       0                     0   
2              0                       0                     0   
3              0                       0                     0   
4              1                       0                     1   

   Windows_type_wooden  
0                    0  
1                    0  
2                    0  
3                    0  
4                    0  

[5 rows x 89 columns]

In [35]:
ml_data.columns[:]

Index(['Id', 'Area', 'build_year', 'building_floors_num', 'rooms_num',
       'Equipment_types_dishwasher', 'Equipment_types_fridge',
       'Equipment_types_furniture', 'Equipment_types_oven',
       'Equipment_types_stove', 'Equipment_types_tv',
       'Equipment_types_washing_machine', 'Extras_types_air_conditioning',
       'Extras_types_attic', 'Extras_types_balcony', 'Extras_types_basement',
       'Extras_types_garage', 'Extras_types_garden', 'Extras_types_lift',
       'Extras_types_separate_kitchen', 'Extras_types_terrace',
       'Extras_types_two_storey', 'Extras_types_usable_room',
       'Media_types_cable-television', 'Media_types_electricity',
       'Media_types_internet', 'Media_types_phone', 'Media_types_sewage',
       'Media_types_water', 'Security_types_alarm',
       'Security_types_anti_burglary_door', 'Security_types_closed_area',
       'Security_types_entryphone', 'Security_types_monitoring',
       'Security_types_roller_shutters', 'floor_num', 'unit_price',


# Selecting best features

In [43]:
counts, bins = np.histogram(ml_data.unit_price, bins=range(0, 50000, 1000))
bins = bins[1:]

fig = px.bar(x=bins, y=counts, labels={'x':'Unit price', 'y':'count'})
fig.show()

In [44]:
X=ml_data.copy()
X=X.query("unit_price<=25000 and unit_price>5000")
y=X.unit_price
X.drop(columns=["unit_price","Id"],inplace=True)

In [45]:
from sklearn.feature_selection import SelectKBest, f_regression, chi2

In [46]:
bestfeatures = SelectKBest(score_func=f_regression, k="all")

In [47]:
fit = bestfeatures.fit(X,y)
dfscores = pd.DataFrame(fit.scores_)
dfcolumns = pd.DataFrame(X.columns)

In [48]:
featureScores = pd.concat([dfcolumns,dfscores],axis=1)
featureScores.columns = ['Specs','Score']

In [49]:
featureScores.nlargest(30,'Score')

Specs        Score
35                   distance_driving  6889.140723
36                   distance_transit  6725.884253
38                       time_transit  5360.201112
37                       time_driving  4741.988679
42                  district_Downtown  3516.937318
40                 district_Bialoleka  1766.097573
75             Building_type_tenement   769.001425
54                     market_primary   701.343385
70                Building_type_block   629.435651
46                  district_Subburbs   582.320969
1                          build_year   515.887396
86                Windows_type_wooden   485.833201
69            Building_type_apartment   432.437679
76   Construction_status_ready_to_use   391.845786
77  Construction_status_to_completion   325.990756
2                 building_floors_num   323.696341
34                          floor_num   315.967698
3                           rooms_num   289.864371
11      Extras_types_air_conditioning   282.383245
52                      district_Wola   265.199542
13               Extras_types_balcony   188.918810
83                      Heating_urban   188.315507
6           Equipment_types_furniture   164.443512
16                Extras_types_garden   162.097546
56            Building_material_brick   158.490793
49                     district_Wawer   153.862225
39                    district_Bemowo   138.977967
67  Building_ownership_full_ownership   128.395893
4          Equipment_types_dishwasher   123.863883
25                  Media_types_phone   121.156862

In [50]:
featureScores.query("Score>40").shape

(51, 2)

In [51]:
top_features=featureScores.nlargest(50,'Score').Specs.unique()

In [52]:
featureScores.sort_values(by="Score",inplace=True,ascending=False)

import plotly.express as px
fig = px.bar(featureScores, x='Specs', y='Score')
fig.show()

In [53]:
X=X[top_features]

## Spliting into train and test sets

In [54]:
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.2, random_state=42)


In [55]:
y_train.reset_index(drop=True,inplace=True)
y_test.reset_index(drop=True,inplace=True)

X_train.reset_index(drop=True,inplace=True)
X_test.reset_index(drop=True,inplace=True)

# Training initial model

In [150]:
from sklearn.ensemble import RandomForestRegressor

## Hyper parameters selection

In [50]:
param_grid = [
   
    
    { "bootstrap":[False],
     "n_estimators":[300],
     "max_features":[10,15,20,30],"max_depth":[10,15,20,25,30],"min_samples_leaf":[3,6,12],"min_samples_split":[6,12,24],
     "min_impurity_decrease":[0.01,0.03,0.1,0.3]
},
    
]

In [90]:
from sklearn.model_selection import GridSearchCV

In [91]:
forest_cl=RandomForestRegressor(random_state=10, n_jobs=2)

In [92]:
grid_search = GridSearchCV(forest_cl, param_grid, cv=4,
                          scoring="neg_mean_absolute_error",return_train_score=True)

In [93]:
#grid_search.fit(X_train, y_train)
#rf_clf_best_params = grid_search.best_estimator_


GridSearchCV(cv=4, error_score=nan,
             estimator=RandomForestRegressor(bootstrap=True, ccp_alpha=0.0,
                                             criterion='mse', max_depth=None,
                                             max_features='auto',
                                             max_leaf_nodes=None,
                                             max_samples=None,
                                             min_impurity_decrease=0.0,
                                             min_impurity_split=None,
                                             min_samples_leaf=1,
                                             min_samples_split=2,
                                             min_weight_fraction_leaf=0.0,
                                             n_estimators=100, n_jobs=2,
                                             oob_score=False, random_...
                                             verbose=0, warm_start=False),
             iid='deprecated', n_jobs=None,
  

In [94]:
grid_search.best_params_

{'max_depth': 20,
 'max_features': 30,
 'min_impurity_decrease': 0.01,
 'min_samples_leaf': 3,
 'min_samples_split': 6,
 'n_estimators': 300}

In [95]:
grid_search.best_params_.keys()

dict_keys(['max_depth', 'max_features', 'min_impurity_decrease', 'min_samples_leaf', 'min_samples_split', 'n_estimators'])

In [151]:
#rf_model=grid_search.best_estimator_

rf_model=RandomForestRegressor(bootstrap=True, ccp_alpha=0.0, criterion='mse',
                      max_depth=20, max_features=30, max_leaf_nodes=None,
                      max_samples=None, min_impurity_decrease=0.01,
                      min_impurity_split=None, min_samples_leaf=3,
                      min_samples_split=6, min_weight_fraction_leaf=0.0,
                      n_estimators=300, n_jobs=2, oob_score=False,
                      random_state=10, verbose=0, warm_start=False)

In [152]:
rf_model.fit(X_train,y_train)

E:\Anaconda\lib\site-packages\ipykernel_launcher.py:1: DataConversionWarning:

A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples,), for example using ravel().



RandomForestRegressor(bootstrap=True, ccp_alpha=0.0, criterion='mse',
                      max_depth=20, max_features=30, max_leaf_nodes=None,
                      max_samples=None, min_impurity_decrease=0.01,
                      min_impurity_split=None, min_samples_leaf=3,
                      min_samples_split=6, min_weight_fraction_leaf=0.0,
                      n_estimators=300, n_jobs=2, oob_score=False,
                      random_state=10, verbose=0, warm_start=False)

In [153]:
rf_model.score(X_train,y_train)

0.8920903621748271

In [154]:
rf_model.score(X_test,y_test)

0.6996631687209058

In [155]:
importance_df=pd.DataFrame(rf_model.feature_importances_,columns=["coefficients"])
importance_df["features"]=X.columns
importance_df.sort_values(by="coefficients",inplace=True)

In [156]:

trace0=go.Bar(
        x=importance_df.coefficients,
        y=importance_df.features,
        orientation="h",
        
        marker=dict(
        color="blue",

        opacity=0.5
        ),
       
    )








data=[trace0]
figure=go.Figure(
    data=data,
    layout=go.Layout(
        title="RF Classifier - Feature importance",
        xaxis=dict(title="Importance"),
        yaxis=dict(title="Feature")

    
    ))
iplot(figure)

In [182]:
def performance_summary(model, X_train,y_train, X_test, y_test ):
    
    y_hat=model.predict(X_test)
    
    df_summary=pd.DataFrame(y_hat, columns=["y_hat"])
    df_summary["y_true"]=y_test
    df_summary["predicted_rank"]=df_summary.y_hat.rank()
    df_summary["abs_error"]=np.abs(df_summary.y_true-df_summary.y_hat)
    df_summary["error"]=df_summary.y_hat-df_summary.y_true
    df_summary["relative_error"]= df_summary["error"]/df_summary.y_true
    df_summary["relative_abs_error"]= df_summary["abs_error"]/df_summary.y_true
    df_summary.sort_values(by="predicted_rank",inplace=True)
    df_summary.reset_index(drop=True, inplace=True)
    
    print("Share of forecasts within 25% absolute error {:.2f}\n".format(df_summary.query("relative_abs_error<0.25").shape[0]/df_summary.shape[0]))
    
    print("Share of forecasts within 10% absolute error {:.2f}\n".format(df_summary.query("relative_abs_error<0.10").shape[0]/df_summary.shape[0]))
    
    print("Share of forecasts within 5% absolute error {:.2f}\n".format(df_summary.query("relative_abs_error<0.05").shape[0]/df_summary.shape[0]))
    
    return(df_summary)
    

## Error analysis

In [183]:
df_summary=performance_summary(rf_model, X_train,y_train, X_test, y_test)

Share of forecasts within 25% absolute error 0.93

Share of forecasts within 10% absolute error 0.68

Share of forecasts within 5% absolute error 0.45



In [159]:
df_summary.describe()

y_hat        y_true  predicted_rank     abs_error         error  \
count   2330.000000   2330.000000     2330.000000   2330.000000   2330.000000   
mean   11120.111575  11115.604721     1165.500000   1050.261141      4.506854   
std     2414.172659   2986.134603      672.757328   1254.823257   1636.485003   
min     5975.218922   5357.000000        1.000000      0.558841 -11303.897948   
25%     9417.619896   9007.750000      583.250000    259.350275   -551.933855   
50%    10915.192480  10698.000000     1165.500000    639.077149     87.453238   
75%    12389.230986  12498.250000     1747.750000   1383.868386    735.655970   
max    23179.475384  25000.000000     2330.000000  11303.897948   9648.903646   

       relative_error  relative_abs_error  
count     2330.000000         2330.000000  
mean         0.019490            0.092267  
std          0.140071            0.107159  
min         -0.480326            0.000038  
25%         -0.048075            0.025319  
50%          0.008700            0.058701  
75%          0.071457            0.123251  
max          1.400828            1.400828

In [160]:
df_summary.head()

y_hat  y_true  predicted_rank    abs_error        error  \
0  5975.218922    6055             1.0    79.781078   -79.781078   
1  6376.263629    6745             2.0   368.736371  -368.736371   
2  6392.824857    5829             3.0   563.824857   563.824857   
3  6437.172603    7726             4.0  1288.827397 -1288.827397   
4  6613.999964    6209             5.0   404.999964   404.999964   

   relative_error  relative_abs_error  
0       -0.013176            0.013176  
1       -0.054668            0.054668  
2        0.096728            0.096728  
3       -0.166817            0.166817  
4        0.065228            0.065228

In [161]:


trace0=go.Scatter(
        name="Predicted",
        y=df_summary.y_true,
        x=df_summary.y_true,
        mode='lines',
        marker=dict(
        size=5,
        opacity=0.3
        ),
       
    )




trace1=go.Scatter(
        name="Actual",
        y=df_summary.y_hat,
        x=df_summary.y_true,
        mode='markers',
        marker=dict(
        color="blue",
    
        size=5,
        opacity=0.1
        ),
        text=df_summary.error
       
    )




data=[trace0,trace1]
figure=go.Figure(
    data=data,
    layout=go.Layout(
        title="Predicted vs actual unit price",
        yaxis=dict(title="Predicted price",range=(0,25000)),
        xaxis=dict(title="Actual price")

    
    ))

iplot(figure)

In [162]:
counts, bins = np.histogram(df_summary.relative_error*100,bins=range(-50,50,2))
counts=counts/df_summary.shape[0]*100
bins=bins[1:]

In [163]:

fig = px.bar(x=bins, y=counts, labels={"x":"relative variance [%]", "y":"count"})
fig.show()

In [164]:
df_summary

y_hat  y_true  predicted_rank    abs_error        error  \
0      5975.218922    6055             1.0    79.781078   -79.781078   
1      6376.263629    6745             2.0   368.736371  -368.736371   
2      6392.824857    5829             3.0   563.824857   563.824857   
3      6437.172603    7726             4.0  1288.827397 -1288.827397   
4      6613.999964    6209             5.0   404.999964   404.999964   
...            ...     ...             ...          ...          ...   
2325  20872.439647   23043          2326.0  2170.560353 -2170.560353   
2326  21043.187119   20204          2327.0   839.187119   839.187119   
2327  21368.665650   19928          2328.0  1440.665650  1440.665650   
2328  23085.404988   24000          2329.0   914.595012  -914.595012   
2329  23179.475384   24500          2330.0  1320.524616 -1320.524616   

      relative_error  relative_abs_error  
0          -0.013176            0.013176  
1          -0.054668            0.054668  
2           0.096728            0.096728  
3          -0.166817            0.166817  
4           0.065228            0.065228  
...              ...                 ...  
2325       -0.094196            0.094196  
2326        0.041536            0.041536  
2327        0.072294            0.072294  
2328       -0.038108            0.038108  
2329       -0.053899            0.053899  

[2330 rows x 7 columns]

# Neural networks models

## Transforming and scaling data for NN

In [145]:
def DNN_plot_loss(history, starting_epoch):

        trace0=go.Scatter(
                y=history.history['loss'][starting_epoch:],
                x=history.epoch[starting_epoch:],
                mode='lines',
                marker=dict(
                color="blue",
                size=5,
                opacity=0.5
                ),
                name="Training Loss"
            )


        trace1=go.Scatter(
                y=history.history['val_loss'][starting_epoch:],
                x=history.epoch[starting_epoch:],
                mode='lines',
                marker=dict(
                color="red",
                size=5,
                opacity=0.5
                ),
                name="Validation Loss"
            )

        data=[trace0, trace1]
        figure=go.Figure(
            data=data,
            layout=go.Layout(
                title="Learning curve",
                yaxis=dict(title="Loss"),
                xaxis=dict(title="Epoch",range=(starting_epoch,history.epoch[-1])),
                legend=dict(
                    x=1,
                    y=1,
                    traceorder="normal",
                    font=dict(
                        family="sans-serif",
                        size=12,
                        color="black"
                    ),
                bgcolor=None


            )))
        iplot(figure)

In [56]:
y_train=np.asarray(y_train).reshape(-1,1)
y_train.shape

(9317, 1)

In [57]:
y_test=np.asarray(y_test).reshape(-1,1)
y_test.shape

(2330, 1)

In [58]:
from sklearn.preprocessing import StandardScaler
scaler = StandardScaler()

In [59]:
X_train=scaler.fit_transform(X_train)
X_test=scaler.transform(X_test)

In [60]:
X_train.shape

(9317, 50)

In [61]:
X_test.shape

(2330, 50)

In [228]:
tf.keras.backend.clear_session()
tf.random.set_seed(60)

DNN=keras.models.Sequential([
    
    keras.layers.Dense(256, input_dim = X_train.shape[1], activation='relu'),
    keras.layers.BatchNormalization(),
    keras.layers.Dropout(0.2),

    keras.layers.Dense(units=256, activation='relu'),
    keras.layers.BatchNormalization(),
    keras.layers.Dropout(0.2),
    
    keras.layers.Dense(units=128, activation='relu'),
    keras.layers.BatchNormalization(),
    keras.layers.Dropout(0.1),
    
    keras.layers.Dense(units=64, activation='relu'),
    keras.layers.Dense(units=1, activation="linear"),



])

In [229]:
DNN.summary()

Model: "sequential"
_________________________________________________________________
Layer (type)                 Output Shape              Param #   
dense (Dense)                (None, 256)               13056     
_________________________________________________________________
batch_normalization (BatchNo (None, 256)               1024      
_________________________________________________________________
dropout (Dropout)            (None, 256)               0         
_________________________________________________________________
dense_1 (Dense)              (None, 256)               65792     
_________________________________________________________________
batch_normalization_1 (Batch (None, 256)               1024      
_________________________________________________________________
dropout_1 (Dropout)          (None, 256)               0         
_________________________________________________________________
dense_2 (Dense)              (None, 128)               3

In [230]:
optimizer = keras.optimizers.Adam()



DNN.compile(optimizer=optimizer, 
            loss='mean_absolute_error',
            metrics=['mean_absolute_error'])


history = DNN.fit(X_train, y_train,
                    epochs=100,
                    validation_data=(X_test, y_test),
                    verbose=1)

Train on 9317 samples, validate on 2330 samples
Epoch 1/100
9317/9317 [==============================] - 3s 369us/sample - loss: 10804.8628 - mean_absolute_error: 10804.8643 - val_loss: 9799.2558 - val_mean_absolute_error: 9799.2549
Epoch 2/100
9317/9317 [==============================] - 3s 283us/sample - loss: 7315.1770 - mean_absolute_error: 7315.1777 - val_loss: 3728.6082 - val_mean_absolute_error: 3728.6082
Epoch 3/100
9317/9317 [==============================] - 2s 230us/sample - loss: 2478.6430 - mean_absolute_error: 2478.6436 - val_loss: 1680.6292 - val_mean_absolute_error: 1680.6290
Epoch 4/100
9317/9317 [==============================] - 2s 223us/sample - loss: 2027.3838 - mean_absolute_error: 2027.3835 - val_loss: 1560.1081 - val_mean_absolute_error: 1560.1080
Epoch 5/100
9317/9317 [==============================] - 2s 222us/sample - loss: 1965.0503 - mean_absolute_error: 1965.0510 - val_loss: 1606.6235 - val_mean_absolute_error: 1606.6237
Epoch 6/100
9317/9317 [============

9317/9317 [==============================] - 2s 226us/sample - loss: 1230.1573 - mean_absolute_error: 1230.1577 - val_loss: 1204.1874 - val_mean_absolute_error: 1204.1874
Epoch 46/100
9317/9317 [==============================] - 2s 226us/sample - loss: 1218.6015 - mean_absolute_error: 1218.6019 - val_loss: 1204.7487 - val_mean_absolute_error: 1204.7483
Epoch 47/100
9317/9317 [==============================] - 2s 227us/sample - loss: 1209.7055 - mean_absolute_error: 1209.7056 - val_loss: 1198.7637 - val_mean_absolute_error: 1198.7637
Epoch 48/100
9317/9317 [==============================] - 2s 232us/sample - loss: 1216.8908 - mean_absolute_error: 1216.8907 - val_loss: 1208.2268 - val_mean_absolute_error: 1208.2267
Epoch 49/100
9317/9317 [==============================] - 2s 225us/sample - loss: 1216.4694 - mean_absolute_error: 1216.4696 - val_loss: 1201.5584 - val_mean_absolute_error: 1201.5588
Epoch 50/100
9317/9317 [==============================] - 2s 232us/sample - loss: 1207.0410 -

9317/9317 [==============================] - 2s 228us/sample - loss: 1103.5293 - mean_absolute_error: 1103.5291 - val_loss: 1166.5472 - val_mean_absolute_error: 1166.5475
Epoch 90/100
9317/9317 [==============================] - 2s 228us/sample - loss: 1115.5005 - mean_absolute_error: 1115.5007 - val_loss: 1156.1625 - val_mean_absolute_error: 1156.1622
Epoch 91/100
9317/9317 [==============================] - 2s 229us/sample - loss: 1107.1721 - mean_absolute_error: 1107.1718 - val_loss: 1178.6036 - val_mean_absolute_error: 1178.6036
Epoch 92/100
9317/9317 [==============================] - 2s 224us/sample - loss: 1087.2770 - mean_absolute_error: 1087.2764 - val_loss: 1182.3581 - val_mean_absolute_error: 1182.3580
Epoch 93/100
9317/9317 [==============================] - 2s 221us/sample - loss: 1091.8859 - mean_absolute_error: 1091.8861 - val_loss: 1172.2344 - val_mean_absolute_error: 1172.2345
Epoch 94/100
9317/9317 [==============================] - 2s 232us/sample - loss: 1080.6990 -

In [232]:
DNN_plot_loss(history,starting_epoch=10)

In [233]:
df_summary_dnn=performance_summary(DNN, X_train,y_train, X_test, y_test)

Share of forecasts within 25% absolute error 0.92

Share of forecasts within 10% absolute error 0.63

Share of forecasts within 5% absolute error 0.39



In [234]:
df_summary_dnn.describe()

y_hat        y_true  predicted_rank     abs_error         error  \
count   2330.000000   2330.000000     2330.000000   2330.000000   2330.000000   
mean   10970.095703  11115.604721     1165.500000   1162.303457   -145.517962   
std     2436.489990   2986.134603      672.757328   1322.690002   1754.951183   
min     5678.835938   5357.000000        1.000000      0.470703 -13311.304688   
25%     9251.155762   9007.750000      583.250000    310.474365   -772.788086   
50%    10796.730469  10698.000000     1165.500000    726.291260     -3.702637   
75%    12167.298340  12498.250000     1747.750000   1527.064941    684.171875   
max    22675.535156  25000.000000     2330.000000  13311.304688   7690.970703   

       relative_error  relative_abs_error  
count     2330.000000         2330.000000  
mean         0.005930            0.100584  
std          0.144375            0.103720  
min         -0.532452            0.000034  
25%         -0.069617            0.029831  
50%         -0.000358            0.069376  
75%          0.068903            0.137517  
max          0.997516            0.997516

In [235]:


trace0=go.Scatter(
        name="Predicted",
        y=df_summary_dnn.y_true,
        x=df_summary_dnn.y_true,
        mode='lines',
        marker=dict(
        size=5,
        opacity=0.3
        ),
       
    )




trace1=go.Scatter(
        name="Actual",
        y=df_summary_dnn.y_hat,
        x=df_summary_dnn.y_true,
        mode='markers',
        marker=dict(
        color="blue",
    
        size=5,
        opacity=0.1
        ),
        text=df_summary_dnn.error
       
    )




data=[trace0,trace1]
figure=go.Figure(
    data=data,
    layout=go.Layout(
        title="Predicted vs actual unit price",
        yaxis=dict(title="Predicted price",range=(0,25000)),
        xaxis=dict(title="Actual price")

    
    ))

iplot(figure)

In [236]:
counts, bins = np.histogram(df_summary_dnn.relative_error*100,bins=range(-50,50,2))
counts=counts/df_summary_dnn.shape[0]*100
bins=bins[1:]

In [237]:

fig = px.bar(x=bins, y=counts, labels={"x":"relative variance [%]", "y":"count"})
fig.show()